In [1]:
import os
import pandas as pd
pd.set_option('display.max_columns', 50)
pd.set_option('display.max_rows', 1000)
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.transforms
plt.style.use('fivethirtyeight')

In [2]:
# Import relevant dataframes:

main_table = pd.read_csv(r"C:\Users\Public\_Data\_Data\Latest_Version\Main_Data\Main_Table_09252019.csv")
print(len(main_table))
faculty_table = pd.read_csv(r"C:\Users\Public\_Data\_Data\Latest_Version\Faculty_Data\Faculty_Table_08272019.csv")
print(len(faculty_table))
skill_table = pd.read_csv(r"C:\Users\Public\_Data\_Data\Latest_Version\Skills_Data\Skill_Table_06072019.csv")
print(len(skill_table))

3957167
3957167
36101672


In [3]:
def title_swap(string):
    dictionary = {'Community and Social Services':'Counseling and Religious Life',
                  'Customer and Client Support':'Online Support and University Information',
                  'Hospitality, Food, and Tourism':'Event Management and Hospitality', 
                  'Planning and Analysis':'Analysis', 
                  'Curriculum and Instructional Designer / Developer':'Curriculum and Instructional Designer', 
                  'Special Education Teacher':'Accessibility and Disability Services', 
                  'Teaching Assistant':'Faculty Support', 
                  'Tutor':'Academic Tutor',
                  'Clerical and Administrative':'Administrative'}
    if(string in dictionary):
        return dictionary[string]
    else:
        return string

In [35]:
def five_percent_threshold(df, category, target, skill_cluster):
    df = df[df[category]==target]
    num_jobs = df['Job ID'].nunique()
    if num_jobs == 0:
        return False
    df = df[df['Skill Cluster Name']==skill_cluster]
    num_with_skill = df['Job ID'].nunique()
    
    incidence = np.true_divide(num_with_skill, num_jobs)
    if incidence >= .05:
        print(str(num_jobs) + '->' + str(num_with_skill))
        return True
    else:
        return False

In [ ]:
# This slide will be reworked in the future:
#     It needs to express the core of the visualization which is to relay the "horizontal" growth to the user.
#     Potentially 3 sections:
#         1) Display new occupations that are requesting the given skill. This should be based on 'entry'
#            into the market for these skills and not the threshold we were previously using
#         2) Growth of career areas/occupations requsting these skills should be displayed
#         3) Absolute size should be displayed in order to represnt which are the dominant sectors
#            requesting this skill

##############################################################################################################

# New Presenataion:
#     Largest Share (In most recent year):
#         Largest incidence rate
        
#     Fastest Growing:
#         List comparatively as barchart
        
#     Within Newest:
#         Largest share
#         Fastest growing

In [ ]:
# New Categories that emerge:

# Greatest (share)
# Fastest
# Newest

In [7]:
# Number of occupation requesting a selected skill in two years

# Skill to run diffusion anaysis on
target_skill = 'Mental and Behavioral Health Specialties'

# Category to break the dataset down by (can be Career Area or Occupation)
category = 'Occupation'

# Chosen years
year1 = 2010
year2 = 2017

if (year1 > year2):
    temp = year1
    year1 = year2
    year2 = temp

# The total set of relevant data which is the skill_table and Occupation/Career Area data from the main_table.
dataframe = skill_table[(skill_table['Year']==year1)|(skill_table['Year']==year2)].merge(
    main_table[(main_table['Year']==year1)|(main_table['Year']==year2)][['Job ID', 'Occupation', 'Career Area']],
    on='Job ID', how='inner')


# Dataframe restricted to the target skill
skill_df = dataframe[dataframe['Skill Cluster Name']==target_skill]

dataframe = dataframe.drop_duplicates('Job ID')
skill_df = skill_df.drop_duplicates('Job ID')

# This is the threshold that we set in order to ensure we have an apporximately normal sample of job postings.
# Any Occupation with fewer than 30 observations in either year will not be counted since the results of the
# 5% incidence test will not be valid

def count_with_skill(df, skill_df, year, cutoff_threshold=30, minimum_incidence=0.05):
    
    # Generate ordered list of the occupations in both years. These show how many obervations within each
    # Occupation request the skill of Fundraising
    cat_skill = pd.DataFrame(skill_df[skill_df['Year']==year][category].value_counts()).reset_index()
    cat_skill = cat_skill.rename(columns={category : '#skill', 'index' : category})
#     display(occ_skill)
    
    cat_df = pd.DataFrame(df[df['Year']==year][category].value_counts().reset_index())
    occ_df = cat_df.rename(columns={category : 'count', 'index' : category})
#     display(occ_df)
    
    cat = cat_df.merge(cat_skill, how='inner', on=category)
    
    cat = cat[cat['count']>=cutoff_threshold]
    
    cat['incidence'] = np.true_divide(cat['#skill'], cat['count'])
    cat = cat.sort_values(by='incidence', ascending=False)
    
    cat = cat[cat['incidence']>=minimum_incidence]
    
    return cat 

# Set the level of occurance that the user would want in order to claim the category requests the skill
desired_incidence = 0.05

# The dataframe of the first year with raw counts and incidneces
counts_1 = count_with_skill(dataframe, skill_df, year1, minimum_incidence=desired_incidence)
counts_1[category] = counts_1[category].apply(title_swap)

# The dataframe of the second year with the same as above
counts_2 = count_with_skill(dataframe, skill_df, year2, minimum_incidence=desired_incidence)
counts_2[category] = counts_2[category].apply(title_swap)

# Perform outer merge on the to dataframes to identify how the job space has changed between
# the sample years
full = counts_1[[category, 'incidence']].merge(counts_2[[category, 'incidence']], on=category, how='outer', indicator=True)

# Utilize indicator from outer merge to identify which categories are newly above the 
# minimum threshold
gained = full[full['_merge']=='right_only']
gained = gained.drop(columns=['incidence_x', '_merge'])
gained = gained.rename(columns={'incidence_y':'incidence'})

# and which categories have falled below in the time period
lost = full[full['_merge']=='left_only']
lost = lost.drop(columns=['incidence_y', '_merge'])
lost = lost.rename(columns={'incidence_x':'incidence'})

# Display all printed output that describes the number of total occupations in both years with the
# target skill, as well as how many came obove the minimum threshold and dropped below it.
print('Skill Analysis: [' + target_skill + ']\n')
print('#', category, str(year1), ':', len(counts_1))
print('#', category, str(year2), ':', len(counts_2))
print(year1, '->', year2, '\n\tNumber of ' + category + 's Added:', len(gained),
      '\n\tNumber of ' + category + 's Dropped:', len(lost))

def incidence_graph(df, category, target_skill, title):
    df = df.sort_values(by='incidence', ascending = False)
    
    rates = df['incidence'][:10].values
    names = df[category][:10].values
    
    ind = np.array([x for x, _ in enumerate(names)])
    
    plt.bar(ind, rates, label='Incidence Rate')
    
    plt.xticks(ind, names, rotation = 'vertical')
    plt.xlabel(category + 's')
    plt.ylabel('Incidence of\n"' + target_skill + '" Skill')
    plt.legend(loc='upper right')
    plt.title(title)
    
    plt.show()

# Display the incidence of the top 10 of the target category in the first year
incidence_graph(counts_1, category, target_skill, 'Top ' + category + 's in ' + str(year1))
print('A ' + category + ' is determined to have the skill if at least ' + str(int(desired_incidence*100)) + '% of its postings demand the desired skill')

# Display for the second year
incidence_graph(counts_2, category, target_skill, 'Top ' + category + 's in ' + str(year2))
print('A ' + category + ' is determined to have the skill if at least ' + str(int(desired_incidence*100)) + '% of its postings demand the desired skill\n')

# Label and display the incidence of the top 10 of the 'Added' buckets in the target category
print(category +'s Added in ' + str(year2) + ' Previously Under Minimum Threshold')
incidence_graph(gained, category, target_skill, 'Top Added ' + category + 's in ' +str(year2))
print('A ' + category + ' is determined to have the skill if at least ' + str(int(desired_incidence*100)) + '% of its postings demand the desired skill')

print("Note: Added refers to an Occupational or Career Area bucket that\n comes above the level of significance "+ 
      "in the second year requested.\nSignificance levels are defined by incidence rates of the skill within the\n " + 
      "Occupation or Career Area and are typically set at 5%.\n" + 
      "An example would be at least 30 jobs in total with 5% of those jobs with the requested skill.")

Skill Analysis: [Mental and Behavioral Health Specialties]

# Occupation 2010 : 103
# Occupation 2017 : 164
2010 -> 2017 
	Number of Occupations Added: 93 
	Number of Occupations Dropped: 32


A Occupation is determined to have the skill if at least 5% of its postings demand the desired skill


A Occupation is determined to have the skill if at least 5% of its postings demand the desired skill

Occupations Added in 2017 Previously Under Minimum Threshold


A Occupation is determined to have the skill if at least 5% of its postings demand the desired skill
Note: Added refers to an Occupational or Career Area bucket that
 comes above the level of significance in the second year requested.
Significance levels are defined by incidence rates of the skill within the
 Occupation or Career Area and are typically set at 5%.
An example would be at least 30 jobs in total with 5% of those jobs with the requested skill.


In [23]:
# Career Areas with the Fastest Growing Demand for Fundrasing Skills

# Minimum incidence rate to be considered for growth calculation. This rate can be seen as a
# category being legitimately related to the chosen skill
minimum_year2_rate = 0.05

# Data needed is the chosen breakdown axis and the skill table restricted to the target skill
df = main_table[['Job ID', category]].merge(skill_table[skill_table['Skill Cluster Name']==target_skill],
                                                        on='Job ID', how='inner')
# Due to the nature of the skills data each job has multiple skills attributed to it. This means
# that in some cases a job will request multiple skills that fall into the category of 
# "Fundraising." Because of the way that skill data is recorded on the skill_table, these show 
# up twice under the same Job ID. If we ignore this problem those jobs would be counted twice in the following
# methods, therefore, they must be removed here.
df = df.drop_duplicates('Job ID')

def get_proportions(year, category, omit=False, cutoff=30):
    """
    get_proportions(year, category, omit=False, cutoff=30)
    
    This function computes and returns the percentage representation of the target skill in the year
    and in the breakdown axis chosen. The category is only considered if it is larger in size
    than 30 observations.
    
    Parameters:
    year (int): The year in which to compute the representative portion of the skill selected.
    category (string): The column in which the output table will be divided by.
    omit (boolean): Whether or not to omit categories below a certain size, or leave them in the
        sample. The omission is performed on the number of observations with the selected skill and 
        not the size of the total category within the category. (default = False)
    cutoff (int): The level that will be the cutoff point if omit == True (default = 30)
    
    Returns:
    (DataFrame): Pandas representation of the categories and the skill percentages within them
    """
    skill = pd.DataFrame(df[df['Year']==year][category].value_counts()).reset_index()
    skill = skill.rename(columns={category :'skill'})

    main = pd.DataFrame(main_table[main_table['Year']==year][category].value_counts()).reset_index()
    main = main.rename(columns={category :'main'})

    full = skill.merge(main, on='index', how='inner')
    if(omit):
        full = full[full['main']>=cutoff]

    full['proportion_'+str(year)] = round(np.true_divide(full['skill'], full['main'])*100, 2)
    full = full.drop(columns=['skill', 'main'])
    
    return full

# Cutoff is based on most recent year ST first year is not filtered
prop_1 = get_proportions(year1, category, omit=False)
# Minimum cutoff is a category size of 30, but better results are achieved if the number is
# much larger than that (~1000)
prop_2 = get_proportions(year2, category, omit=True, cutoff=1000)

prop_total = prop_1.merge(prop_2, on='index', how='inner')
prop_total['index'] = prop_total['index'].apply(title_swap)

# Compute growth between years
prop_total['growth'] = round(np.true_divide(prop_total['proportion_' + str(year2)]-prop_total['proportion_' + str(year1)], 
                                      prop_total['proportion_' + str(year1)])*100, 2)
# Remove categories with year 2 prop < minimum rate
prop_total = prop_total[prop_total['proportion_' + str(year2)]>(minimum_year2_rate * 100)]

# Sort by growth and display table
prop_total = prop_total.sort_values(by='growth', ascending=False).reset_index(drop=True)

prop_total = prop_total.rename(columns={'index' : category})

print('Growth of ' + target_skill + ' within ' + category + 's from ' + str(year1) + ' to ' + str(year2))
display(prop_total[:10])

def display_growth(df, category, target_skill, title):
    
    rates = df['growth'][:10].values
    names = df[category][:10].values
    ind = np.array([x for x, _ in enumerate(names)])
    
    plt.bar(ind, rates, label='Growth Rate (%)')
    
    plt.xticks(ind, names, rotation='vertical')
    plt.xlabel(category + 's')
    plt.ylabel('Percentage Growth Rate')
    plt.legend(loc='upper right')
    plt.title(title)
    
    plt.show()
    
display_growth(prop_total, category, target_skill, 'Growth of top ' + category + 's\nwith skill: ' + target_skill)

Growth of Mental and Behavioral Health Specialties within Occupations from 2010 to 2017


Occupation  proportion_2010  proportion_2017  \
0                            Nurse Manager             2.87            17.11   
1                Dean of Academic Division             2.17             5.36   
2    Program Coordinator, Higher Education             3.35             6.96   
3              Director of Student Affairs             4.06             7.72   
4                Education Program Manager             4.05             6.54   
5            Preschool / Childcare Teacher             4.18             6.55   
6           Nursing Instructor / Professor             5.87             8.92   
7                       Nurse Practitioner             7.32            11.05   
8  Family / School / General Social Worker            27.52            41.36   
9                 Healthcare Administrator            10.01            14.41   

   growth  
0  496.17  
1  147.00  
2  107.76  
3   90.15  
4   61.48  
5   56.70  
6   51.96  
7   50.96  
8   50.29  
9   43.96

In [ ]:
# TODO: 
#     Generate "heatmap" of the number of times a skill appears in a job posting type. This would be an average
#     of the number of times this kind of skill appears within occupation



In [13]:
# Relative Faculty Breakdowns

year_1 = 2010
year_2 = 2017

fac = faculty_table[['Faculty', 'Job ID', 'Year', 'Tenure_Line', 'Contingent',
                     'Full-time Contingent', 'Part-time Contingent']]
fac = fac[fac['Faculty']==1]
fac = fac.drop(columns='Faculty')

classification = main_table[['Job ID', '4-year', '2-year', 'Public', 'Private', 'R1']]

table = fac.merge(classification, on='Job ID', how='inner')

def summation(year, all=True, four=True, two=True, public=True, private=True, R1=False):
    """
    summation(year, all=True, four=False, two=False, public=False, private=False, R1=False)
    
    This function uses the properties of dummy variables to obtain aggregate values of
    faculty postings. The entire faculty table is filtered and then summed to gain the
    relevant numbers.
    
    Parameters:
    year (int): year in which to perform the summation
    all (boolean): Whether or not to use all faculty observations, or to choose some
        subset of that. If True, all the other parameters are ignored.
    four (boolean): Use 4-year institutions?
    two  (boolean): Use 2-year institutions?
    public  (boolean): Use Public institutions?
    private (boolean): Use Private institutions?
    R1 (boolean): Use only R1 institutions?
    
    Returns:
    (DataFrame): Pandas representation of the 4 relevant categories and their counts.
    """
    temp = table[table['Year']==year]
    
    if(not(all)):
        temp = temp[~((temp['4-year']==0)
                     &(temp['2-year']==0)
                     &(temp['Public']==0)
                     &(temp['Private']==0)
                     &(temp['R1']==0))]
        if(not(four)):
            temp = temp[~(temp['4-year']==1)]
        if(not(two)):
            temp = temp[~(temp['2-year']==1)]
        if(not(public)):
            temp = temp[~(temp['Public']==1)]
        if(not(private)):
            temp = temp[~(temp['Private']==1)]
        if(not(R1)):
            temp = temp[~(temp['R1']==1)]
            
    temp = pd.DataFrame(temp[['Tenure_Line', 'Contingent', 'Full-time Contingent', 'Part-time Contingent']].sum())
    temp = temp.rename(columns={0:'count'})
    
    return temp

sum_1 = summation(year_1, all=False, two=False)
sum_2 = summation(year_2, all=False, two=False)
                  
def adjust(df):
    """
    adjust(df)
    
    This function performs the FTC and PTC adjustment process such that FTC + PTC + TL = 100%.
    
    Parameters:
    df (DataFrame): Any DataFrame containing the 4 faculty types that needs to be adjusted to
        represent realistic contingent breakdowns.
        
    Returns:
    (DataFrame): The adjusted DataFrame.
    """
    specific_contingent_count = df.loc['Full-time Contingent'] + df.loc['Part-time Contingent']
    contingent_count = df.loc['Contingent']

    df.loc['Full-time Contingent'] = round((df.loc['Full-time Contingent'] / specific_contingent_count)
                                           * contingent_count)
    df.loc['Part-time Contingent'] = round((df.loc['Part-time Contingent'] / specific_contingent_count)
                                           * contingent_count)
    df = df.drop(index='Contingent')

    total = df['count'].sum()
    df['prop'] = round(np.true_divide(df['count'], total)*100, 2)
    
    return df

final_1 = adjust(sum_1)
final_2 = adjust(sum_2)

print(year_1)
display(final_1)
print(year_2)
display(final_2)

2010


count   prop
Tenure_Line           11681.0  51.63
Full-time Contingent   6105.0  26.98
Part-time Contingent   4840.0  21.39

2017


count   prop
Tenure_Line           16262.0  38.48
Full-time Contingent  12018.0  28.44
Part-time Contingent  13978.0  33.08

In [3]:
target = 'Fundraising Manager'
category = 'Skill Name'
year1 = 2010
year2 = 2017

main_df = main_table[main_table['Occupation']==target]
main_df = main_df[(main_df['Year']==year1)|(main_df['Year']==year2)]

skill_df = skill_table[(skill_table['Year']==year1)|(skill_table['Year']==year2)]

def get_proportions(main_df, skill_df, year, omit=False, cutoff=30):
    
    main_df = main_df[main_df['Year']==year]
    num_occ = main_df['Job ID'].nunique()
    
    skill_df = skill_df[skill_df['Year']==year]
    total_df = main_df.merge(skill_df, on='Job ID', how='inner')
    
    skills = pd.DataFrame(total_df[category].value_counts()).reset_index()
    skills = skills.rename(columns={category:'count', 'index':category})
    
    if(omit):
        skills = skills[skills['count']>=cutoff]
        
    skills['proportion_'+str(year)] = np.true_divide(skills['count'], num_occ)
#     skills = skills.drop(columns=['count'])
    
    return skills

prop_1 = get_proportions(main_df, skill_df, year1, omit=False)

prop_2 = get_proportions(main_df, skill_df, year2, omit=True, cutoff = 100)

prop_total = prop_1.merge(prop_2, on=category, how='inner')

prop_total['growth'] = round(np.true_divide(prop_total['proportion_' + str(year2)]-prop_total['proportion_' + str(year1)], 
                                      prop_total['proportion_' + str(year1)])*100, 2)

prop_total.sort_values(by='growth', ascending=False).reset_index(drop=True)

Skill Name  count_x  proportion_2010  count_y  \
0                             Typing       10         0.003644      135   
1                       Social Media       35         0.012755      345   
2                 Physical Abilities       54         0.019679      365   
3                  Critical Thinking       30         0.010933      185   
4                   Direct Marketing       22         0.008017      108   
5                    Data Management       29         0.010569      141   
6                       Patient Care       23         0.008382      105   
7                   Progress Reports       34         0.012391      124   
8                      Raiser's Edge      104         0.037901      376   
9                    Detail-Oriented      270         0.098397      833   
10                Prioritizing Tasks       52         0.018950      155   
11              Microsoft Powerpoint      136         0.049563      402   
12                        Initiative       46         0.016764      134   
13  Building Effective Relationships      409         0.149052     1189   
14                        Scheduling       89         0.032434      257   
15                   Problem Solving      173         0.063047      497   
16                         Listening       56         0.020408      160   
17                         Mentoring       87         0.031706      241   
18                     Multi-Tasking       95         0.034621      257   
19                      Self-Starter      105         0.038265      277   
20                        Persuasion      121         0.044096      319   
21          Teamwork / Collaboration      676         0.246356     1781   
22                        Leadership      100         0.036443      262   
23                 Meeting Deadlines      141         0.051385      366   
24                Strategic Planning      247         0.090015      626   
25                Project Management      180         0.065598      455   
26                   Microsoft Excel      308         0.112245      746   
27                    Microsoft Word      167         0.060860      403   
28               Presentation Skills      123         0.044825      287   
29                  Microsoft Office      341         0.124271      760   
30                  Customer Service       77         0.028061      166   
31             Strategic Development       72         0.026239      154   
32                          Research      895         0.326166     1897   
33                    Event Planning      117         0.042638      247   
34           Business Administration       71         0.025875      148   
35                             Sales       60         0.021866      125   
36                         Energetic       84         0.030612      174   
37                   Public Speaking       65         0.023688      132   
38               Preparing Proposals      168         0.061224      340   
39                        Accounting       87         0.031706      176   
40                   Time Management      167         0.060860      335   
41                      Spreadsheets      107         0.038994      214   
42                           Editing      175         0.063776      349   
43                   Word Processing       83         0.030248      164   
44                       Fundraising     1721         0.627187     3332   
45                       Newsletters       77         0.028061      149   
46                           Writing      750         0.273324     1445   
47                         Budgeting      652         0.237609     1250   
48                      Goal Setting       57         0.020773      109   
49                        Creativity      451         0.164359      845   
50                  Staff Management      394         0.143586      735   
51       Verbal / Oral Communication      156         0.056851      291   
52                     Grant Writing      185      

In [20]:
main_table[main_table['Occupation']=='Fundraising Manager']

Unnamed: 0  Unnamed: 0.1       Job ID  Year  \
80               80            80         5076  2011   
136             136           136         5154  2011   
199             199           199         5570  2011   
265             265           265         8878  2011   
303             303           303        13331  2011   
399             399           399        23507  2011   
535             535           535        29740  2011   
537             537           537        29747  2011   
538             538           538        29759  2011   
539             539           539        29767  2011   
540             540           540        29768  2011   
693             693           693        37860  2011   
783             783           783        50084  2011   
867             867           867        51529  2011   
1129           1129          1129        72583  2011   
1143           1143          1143        74360  2011   
1144           1144          1144        74361  2011   
1158           1158          1158        74385  2011   
1159           1159          1159        74386  2011   
1220           1220          1220        83076  2011   
1297           1297          1297        90827  2011   
1671           1671          1671       279320  2011   
2613           2613          2613       333414  2011   
2715           2715          2715       333600  2011   
2724           2724          2724       333611  2011   
2754           2754          2754       333655  2011   
2921           2921          2921       333911  2011   
2974           2974          2974       333999  2011   
2990           2990          2990       334029  2011   
3232           3232          3232       378764  2011   
3268           3268          3268       379160  2011   
3410           3410          3410       418018  2011   
3435           3435          3435       420212  2011   
3496           3496          3496       423492  2011   
3498           3498          3498       423552  2011   
3500           3500          3500       423557  2011   
3502           3502          3502       423565  2011   
3503           3503          3503       423567  2011   
3765           3765          3765       450079  2011   
3768           3768          3768       450082  2011   
3779           3779          3779       450097  2011   
3870           3870          3870       456473  2011   
4054           4054          4054       500242  2011   
4189           4189          4189       511811  2011   
4254           4254          4254       517374  2011   
4328           4328          4328       517499  2011   
4332           4332          4332       517504  2011   
4365           4365          4365       517551  2011   
4376           4376          4376       517570  2011   
4388           4388          4388       517599  2011   
4604           4604          4604       570661  2011   
4613           4613          4613       571495  2011   
4751           4751          4751       612166  2011   
4918           4918          4918       637009  2011   
5005           5005          5005       642275  2011   
5037           5037          5037       642733  2011   
5044           5044          5044       643967  2011   
5045           5045          5045       643971  2011   
5155           5155          5155       658456  2011   
5165           5165          5165       658604  2011   
5668           5668          5668       668923  2011   
5772           5772          5772       669076  2011   
5792           5792          5792       669098  2011   
6017           6017          6017       715784  2011   
6018           6018          6018       715814  2011   
6019           6019          6019       715818  2011   
6021           6021          6021       715825  2011   
6022           6022          6022       715837  2011   
6023           6023          6023       715838  2011   
6024           6024          6024       715843  2011   
6074           6074          6074

In [73]:
main_table[(main_table['Private']==1)&(main_table['4-year']==0)&(main_table['2-year']==0)&(main_table['Public']==0)&(main_table['R1']==0)]

Unnamed: 0       Job ID  Year  \
1693148     1693148    340889586  2013   
1693149     1693149    340889811  2012   
1693150     1693150    340890062  2013   
1693151     1693151    340890063  2013   
1693152     1693152    340890064  2013   
1693153     1693153    340890065  2013   
1693154     1693154    340890067  2013   
1693156     1693156    340891036  2013   
1693164     1693164    340893577  2013   
1693165     1693165    340893578  2013   
1693166     1693166    340893581  2013   
1693168     1693168    340916348  2012   
1693169     1693169    340916525  2013   
1693170     1693170    340918106  2013   
1693173     1693173    340947199  2013   
1693177     1693177    340949036  2013   
1693178     1693178    340949037  2013   
1693183     1693183    340950135  2013   
1693184     1693184    340950136  2013   
1693190     1693190    340954569  2013   
1693192     1693192    340956175  2013   
1693193     1693193    340957059  2013   
1693203     1693203    340964506  2013   
1693207     1693207    340965978  2013   
1693208     1693208    340965979  2013   
1693209     1693209    340965981  2013   
1693210     1693210    340966455  2013   
1693211     1693211    340966458  2013   
1693213     1693213    340966984  2013   
1693215     1693215    340967918  2013   
1708216     1708216    346256526  2013   
1708218     1708218    346256870  2013   
1708219     1708219    346256873  2013   
1708220     1708220    346256874  2013   
1708221     1708221    346256875  2013   
1708222     1708222    346256881  2013   
1708223     1708223    346256882  2013   
1708224     1708224    346256883  2013   
1708225     1708225    346256948  2013   
1708226     1708226    346257044  2013   
1708228     1708228    346257477  2013   
1708229     1708229    346257510  2013   
1708230     1708230    346257564  2013   
1708231     1708231    346257576  2013   
1708232     1708232    346257577  2013   
1708233     1708233    346257578  2013   
1708234     1708234    346257579  2013   
1708235     1708235    346257584  2013   
1708236     1708236    346258066  2013   
1708237     1708237    346258332  2013   
1708238     1708238    346258333  2013   
1708239     1708239    346258336  2013   
1708240     1708240    346258337  2013   
1708241     1708241    346258338  2013   
1708243     1708243    346260422  2013   
1766013     1766013    400745105  2013   
1766015     1766015    400750118  2013   
1766016     1766016    400750436  2013   
1766017     1766017    400764682  2013   
1766020     1766020    400767821  2013   
1766027     1766027    400772684  2013   
1766028     1766028    400773129  2013   
1766029     1766029    400773130  2013   
1766030     1766030    400773131  2013   
1766031     1766031    400773132  2013   
1766032     1766032    400773133  2013   
1766033     1766033    400773134  2013   
1766034     1766034    400773135  2013   
1766035     1766035    400773136  2013   
1766036     1766036    400773137  2013   
1766037     1766037    400773138  2013   
1766038     1766038    400773139  2013   
1766039     1766039    400773140  2013   
1766043     1766043    400785293  2013   
1766044     1766044    400789913  2013   
1766045     1766045    400789919  2013   
1766046     1766046    400789928  2013   
1766047     1766047    400789930  2013   
1766048     1766048    400789935  2013   
1766049     1766049    400789936  2013   
1766050     1766050    400794998  2013   
1766051     1766051    400797509  2013   
1766052     1766052    400797511  2013   
1766053     1766053    400797512  2013   
1766059     1766059    400808644  2013   
1766060     1766060    400810751  2013   
1766061     1766061    400810753  2013   
1766065     1766065    400812415  2013   
1766066     1766066    400812848  2013   
1766067     1766067    400812850  2013   
1766068     1766068    400812854  2013   
1766069     1766069    400812855  2013   
1766076     1766076    400823268  2013   
1766077     1766077    400826130  2013   
1766078     1766078

In [4]:
table = main_table[main_table['Job Title'].str.contains('cife director', case=False, na=False)]

table

Unnamed: 0       Job ID  Year      Job Title Occupation Career Area  \
3415261     3415261  38170914036  2017  Cife Director         na          na   
3417160     3417160  38171177381  2017  Cife Director         na          na   
3422501     3422501  38172415042  2017  Cife Director         na          na   
3727666     3727666  38262321426  2017  Cife Director         na          na   

         Minimum EDU Requirements  Maximum EDU Requirements  \
3415261                        21                      -999   
3417160                        21                      -999   
3422501                        21                      -999   
3727666                        21                      -999   

         Minimum Experience Requirements  Annual Salary  \
3415261                           -83.25         -999.0   
3417160                           -83.25         -999.0   
3422501                           -83.25         -999.0   
3727666                           -83.25         -999.0   

        Metropolitan Statistical Area         State  \
3415261             State College, PA  Pennsylvania   
3417160             State College, PA  Pennsylvania   
3422501                Pittsburgh, PA  Pennsylvania   
3727666                            na  Pennsylvania   

                                    IPEDS Institution Name  \
3415261          Pennsylvania State University-Main Campus   
3417160          Pennsylvania State University-Main Campus   
3422501  Pennsylvania State University-Penn State New K...   
3727666                                                NaN   

               IPEDS Sector Name  R1  4-year  2-year  Public  Private  
3415261  Public, 4-year or above   1       1       0       1        0  
3417160  Public, 4-year or above   1       1       0       1        0  
3422501  Public, 4-year or above   0       1       0       1        0  
3727666  Public, 4-year or above   0       1       0       1        0

In [10]:
table = main_table[main_table['Job Title'].str.contains('legacy staff', case=False, na=False)]
table = table[table['Year']==2017]
table = table[table['Occupation']=='na']

print(len(table))
table.sort_values(by='Metropolitan Statistical Area')

44


Unnamed: 0       Job ID  Year     Job Title Occupation Career Area  \
3869426     3869426  38292824466  2017  Legacy Staff         na          na   
3654429     3654429  38247274893  2017  Legacy Staff         na          na   
3874850     3874850  38294180041  2017  Legacy Staff         na          na   
3876067     3876067  38294500995  2017  Legacy Staff         na          na   
3884869     3884869  38296344436  2017  Legacy Staff         na          na   
3885925     3885925  38296646282  2017  Legacy Staff         na          na   
3588633     3588633  38226114993  2017  Legacy Staff         na          na   
3753540     3753540  38266370302  2017  Legacy Staff         na          na   
3865768     3865768  38292382510  2017  Legacy Staff         na          na   
3832074     3832074  38284824150  2017  Legacy Staff         na          na   
3820300     3820300  38282108730  2017  Legacy Staff         na          na   
3803857     3803857  38278106075  2017  Legacy Staff         na          na   
3803164     3803164  38278016287  2017  Legacy Staff         na          na   
3496667     3496667  38196888338  2017  Legacy Staff         na          na   
3791001     3791001  38275075654  2017  Legacy Staff         na          na   
3525079     3525079  38206344643  2017  Legacy Staff         na          na   
3703790     3703790  38258873748  2017  Legacy Staff         na          na   
3791955     3791955  38275292527  2017  Legacy Staff         na          na   
3866054     3866054  38292407826  2017  Legacy Staff         na          na   
3655293     3655293  38247429928  2017  Legacy Staff         na          na   
3654946     3654946  38247351018  2017  Legacy Staff         na          na   
3938395     3938395  38309503176  2017  Legacy Staff         na          na   
3588642     3588642  38226115627  2017  Legacy Staff         na          na   
3939202     3939202  38309728895  2017  Legacy Staff         na          na   
3703618     3703618  38258870689  2017  Legacy Staff         na          na   
3947542     3947542  38311469514  2017  Legacy Staff         na          na   
3948037     3948037  38311615285  2017  Legacy Staff         na          na   
3869764     3869764  38292955311  2017  Legacy Staff         na          na   
3535506     3535506  38209502150  2017  Legacy Staff         na          na   
3619340     3619340  38237036467  2017  Legacy Staff         na          na   
3540505     3540505  38210797413  2017  Legacy Staff         na          na   
3440014     3440014  38177951222  2017  Legacy Staff         na          na   
3761425     3761425  38267945178  2017  Legacy Staff         na          na   
3591210     3591210  38227207612  2017  Legacy Staff         na          na   
3868160     3868160  38292714612  2017  Legacy Staff         na          na   
3834826     3834826  38285414774  2017  Legacy Staff         na          na   
3833859     3833859  38285187374  2017  Legacy Staff         na          na   
3950007     3950007  38312012510  2017  Legacy Staff         na          na   
3657533     3657533  38248149452  2017  Legacy Staff         na          na   
3572353     3572353  38220304094  2017  Legacy Staff         na          na   
3449518     3449518  38180777886  2017  Legacy Staff         na          na   
3950701     3950701  38312158676  2017  Legacy Staff         na          na   
3887389     3887389  38297042964  2017  Legacy Staff         na          na   
3533973     3533973  38209116288  2017  Legacy Staff         na          na   

         Minimum EDU Requirements  Maximum EDU Requirements  \
3869426                        16                        21   
3654429                        16                        21   
3874850                        16                        21   
3876067                        16                        21   
3884869                        21                      -999   
3885925                        21                      -999   
3588633     

In [6]:
table = main_table[main_table['Job Title']=='Legacy Staff']

table

Unnamed: 0       Job ID  Year     Job Title Occupation Career Area  \
406801       406801    120015511  2012  Legacy Staff         na          na   
426203       426203    121531921  2012  Legacy Staff         na          na   
530212       530212    133088694  2012  Legacy Staff         na          na   
716137       716137    148598633  2012  Legacy Staff         na          na   
786919       786919    239088910  2013  Legacy Staff         na          na   
786929       786929    239089979  2013  Legacy Staff         na          na   
817017       817017    243285021  2013  Legacy Staff         na          na   
833008       833008    245451288  2013  Legacy Staff         na          na   
867588       867588    250310465  2013  Legacy Staff         na          na   
867591       867591    250310577  2013  Legacy Staff         na          na   
908268       908268    255745968  2013  Legacy Staff         na          na   
1702437     1702437    345192970  2013  Legacy Staff         na          na   
1703953     1703953    345564671  2013  Legacy Staff         na          na   
1736305     1736305    354486193  2013  Legacy Staff         na          na   
1758922     1758922    358576912  2013  Legacy Staff         na          na   
1812547     1812547    419381106  2013  Legacy Staff         na          na   
1905236     1905236    430973552  2014  Legacy Staff         na          na   
1956281     1956281    438333339  2014  Legacy Staff         na          na   
1964797     1964797    439381067  2014  Legacy Staff         na          na   
2005430     2005430    744816474  2014  Legacy Staff         na          na   
2051517     2051517  25389361377  2014  Legacy Staff         na          na   
2092307     2092307  37810884249  2014  Legacy Staff         na          na   
2113583     2113583  37813986668  2014  Legacy Staff         na          na   
2133412     2133412  37817010714  2014  Legacy Staff         na          na   
2194963     2194963  37831494879  2014  Legacy Staff         na          na   
2203832     2203832  37833177337  2014  Legacy Staff         na          na   
2205316     2205316  37833513539  2014  Legacy Staff         na          na   
2205910     2205910  37833599118  2014  Legacy Staff         na          na   
2280613     2280613  37848247219  2014  Legacy Staff         na          na   
2283380     2283380  37848753266  2014  Legacy Staff         na          na   
2288021     2288021  37849835412  2014  Legacy Staff         na          na   
2310922     2310922  37854852368  2014  Legacy Staff         na          na   
2319305     2319305  37857420593  2014  Legacy Staff         na          na   
2373221     2373221  37871855887  2015  Legacy Staff         na          na   
2376644     2376644  37872847869  2015  Legacy Staff         na          na   
2376656     2376656  37872852017  2015  Legacy Staff         na          na   
2483680     2483680  37903384435  2015  Legacy Staff         na          na   
2514604     2514604  37911469462  2015  Legacy Staff         na          na   
2579830     2579830  37929773685  2015  Legacy Staff         na          na   
2598481     2598481  37934804164  2015  Legacy Staff         na          na   
2605107     2605107  37937187556  2015  Legacy Staff         na          na   
2709132     2709132  37962367815  2015  Legacy Staff         na          na   
2719814     2719814  37964626429  2015  Legacy Staff         na          na   
2726269     2726269  37966121068  2015  Legacy Staff         na          na   
2732016     2732016  37967745427  2015  Legacy Staff         na          na   
2734006     2734006  37968224806  2015  Legacy Staff         na          na   
2802136     2802136  37987418910  2015  Legacy Staff         na          na   
2808262     2808262  37988559098  2015  Legacy Staff         na          na   
2812932     2812932  37989777794  2015  Legacy Staff         na          na   
2909237     2909237  38021534616  2016  Legacy Staff       

In [15]:
for column in skill_table.columns:
    print(column)

Unnamed: 0
Unnamed: 0.1
Job ID
Year
Skill Name
Is Specialized Skill?
Is Software Skill?
Skill Cluster Name


In [41]:
# Number of occupation requesting a selected skill in two years

# Chosen years
year1 = 2010
year2 = 2017

# The total set of relevant data which is the skill_table and Occupation/Career Area data from the main_table.
dataframe = skill_table[(skill_table['Year']==year1)|(skill_table['Year']==year2)].merge(
    main_table[(main_table['Year']==year1)|(main_table['Year']==year2)][['Job ID', 'Occupation', 'Career Area']],
    on='Job ID', how='inner').drop_duplicates('Job ID')

# Target skill
skill = 'Fundraising'

# Dataframe restricted to the target skill
skill_df = dataframe[dataframe['Skill Cluster Name']==skill]


# This is the threshold that we set in order to ensure we have an apporximately normal sample of job postings.
# Any Occupation with fewer than 50 observations in either year will not be counted since the results of the
# 5% incidence test will not be valid

def count_with_skill(df, skill_df, year, cutoff_threshold=30):
    
    # Generate ordered list of the occupations in both years. These show how many obervations within each
    # Occupation request the skill of Fundraising
    occ = pd.DataFrame(skill_df[skill_df['Year']==year]['Occupation'].value_counts()).reset_index()
    occ = occ.rename(columns={'Occupation':'count', 'index':'Occupation'})
    
    df = df[df['Year']==year]
    count = 0
    for index, row in occ.iterrows():
        # The cutoff threshold is needed in order to make the sample approximately normal and representative
        # of the population of jobs in that occupation. This will make the estimate of the 5% threshold a 
        # valid discriminator.
        if(row['count'] < cutoff_threshold):
            break
        # This threshold is used to count only those jobs with a fairly significant level of postings
        # requesting fundraising skills.
        print(row['Occupation'])
        if(five_percent_threshold(df, 'Occupation', row['Occupation'], skill)):
            count += 1
    return count    

count_year1 = count_with_skill(dataframe, skill_df, year1)
print('# Occupations ' + str(year1) + ':', count_year1, '\n')

count_year2 = count_with_skill(dataframe, skill_df, year2)
print('# Occupations ' + str(year2) + ':', count_year2)


# This slide will be reworked in the future:
#     It needs to express the core of the visualization which is to relay the "horizontal" growth to the user.
#     Potentially 3 sections:
#         1) Display new occupations that are requesting the given skill. This should be based on 'entry'
#            into the market for these skills and not the threshold we were previously using
#         2) Growth of career areas/occupations requsting these skills should be displayed
#         3) Absolute size should be displayed in order to represnt which are the dominant sectors
#            requesting this skill

##############################################################################################################

# For Nina and CS Team:
#     This slide will have some changes come to it in the future. in the meantime, try and get a visual part
#     of it working. We ask this of you since not all of it will change, and it is best that you begin working
#     on it now rather than waiting for the final version.


Fundraising Manager
2744->320
na
Coach
Fundraising / Development Specialist
519->33
Administrative Manager
Executive Director
390->30
# Occupations 2010: 3 

Fundraising Manager
4672->513
Coach
na
Fundraising / Development Specialist
1151->94
Administrator, Higher Education
Dean of Academic Division
Administrative Manager
Alumni Relations Manager
598->40
# Occupations 2017: 3
